# Определение стоимости автомобилей

Сервис по продаже автомобилей с пробегом «Не бит, не крашен» разрабатывает приложение для привлечения новых клиентов. В нём можно быстро узнать рыночную стоимость своего автомобиля. В вашем распоряжении исторические данные: технические характеристики, комплектации и цены автомобилей. Вам нужно построить модель для определения стоимости. 

Заказчику важны:

- качество предсказания;
- скорость предсказания;
- время обучения.

## Подготовка данных

In [1]:
import pandas as pd
import numpy as np

!pip install pandas-profiling[notebook]
!jupyter nbextension enable --py widgetsnbextension
import pandas_profiling
import math

from sklearn.model_selection import train_test_split, GridSearchCV

from sklearn.metrics import mean_squared_error, make_scorer

from sklearn.tree import DecisionTreeRegressor
from catboost import CatBoostRegressor, Pool
from lightgbm import LGBMRegressor

import warnings
warnings.filterwarnings('ignore')

Enabling notebook extension jupyter-js-widgets/extension...
      - Validating: OK


/tmp/ipykernel_425/2189061019.py:6: DeprecationWarning: `import pandas_profiling` is going to be deprecated by April 1st. Please use `import ydata_profiling` instead.
  import pandas_profiling


In [2]:
df = pd.read_csv('/datasets/autos.csv')

In [3]:
pandas_profiling.ProfileReport(df, title = 'Pandas Profiling Report')

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

<b>Вывод по профайлингу:</b>
   1. Столбец с количеством фотографий автомобиля имеет константное значение - 0
   2. Большое количество пропусков в столбах (от 3% до 20%)
   3. Столбец мощности и года регистрации автомобиля коррелирует со столбцом цены
   4. В столбце даты скачивания анкеты из базы 271174 уникальных значения. В столбце последней активности пользователя - 179150
   5. В столбцах мощности и даты регистрации автомобиля слишком большой разброс данных.

<b>Предобработка данных</b>

Удалим столбцы, которые нам не нужны для обучения модели и носят декартивно-информативный характер.

In [4]:
df = df.drop(['DateCrawled','DateCreated', 'NumberOfPictures', 'PostalCode', 'LastSeen', 'RegistrationMonth'], axis = 1)

Удалим дубликаты.

In [5]:
df = df.drop_duplicates()

Заполним пропуски.
Столбец Repaired заполним значением 'no'. Остальные столбцы заполним модой (самым часто встречающимся значением). Удаление пропусков привело бы к 20% потере данных, чего допускать нельзя.

In [6]:
df['Repaired'] = df['Repaired'].fillna('no')

df['VehicleType'] = df['VehicleType'].fillna(df['VehicleType'].mode().values[0])
df['Model'] = df['Model'].fillna(df['Model'].mode().values[0])
df['Gearbox'] = df['Gearbox'].fillna(df['Gearbox'].mode().values[0])
df['FuelType'] = df['FuelType'].fillna(df['FuelType'].mode().values[0])

Избавимся от выбросов и аномальных значений

In [7]:
def year(value):
    if value > 2016:
        return 2016
    elif value < 1945:
        return 1945
    else:
        return value

df['RegistrationYear'] = df['RegistrationYear'].apply(year)

# В стобцe Power (мощность двигателя) есть аномальные нулевые и крайне большие значения. Можно попробовать с ними работать как с пропусками - заполнить такие значения медианными по группе (модель / марка авто)
df.loc[ df['Power'] == 0, 'Power'] = float('nan')
df['Power'] = df['Power'].fillna(df.groupby(['Brand', 'Model'])['Power'].transform('median'))
#то, что не удалось заменить, заполним медианой
df['Power'] = df['Power'].fillna(df['Power'].median())
# в столбце Power остались аномальные значения. Оставим их в промежутке [0.05 квантиль; 0.95 квантиль] или [54;218]
df = df.query('54 <= Power <= 350')

df = df.query('200 <= Price <= 14600')

Для экономии памяти заменим тип данных.

In [8]:
df['Price'] = df['Price'].astype('int32')
df['RegistrationYear'] = df['RegistrationYear'].astype('int16')
df['Kilometer'] = df['Kilometer'].astype('int32')

<div class='alert alert-success'> ✔️Молодец, что стараешься экономить память. В дальнейшем можешь использовать функцию Pandas  <a href='https://zen.yandex.ru/media/id/5ee6f73b7cadb75a66e4c7e3/opredelenie-granic-chislovyh-tipov-s-pandas-i-numpy-6210ea6f4da4d749364d96dd'> to_numeric, которая сама поможет найти оптимальный тип <a>.


</div>

<b>Вывод по 1 главе:</b>
1. Выведены и обработаны аномальные и пропущенные значения;
2. Отобраны небходимые столбцы для обучения модели;
3. Сэкономлено 5MB данных.

## Обучение моделей

Так как некоторые модели не умеют работать с категориальными признаками, нужно применить One-Hot Encoding.

In [9]:
df_ohe = pd.get_dummies(df, drop_first = True)

<div class='alert alert-warning'>⚠️
Хорошо, что в get_dummies используешь параметр  drop_first=True, который позволяет избавиться от фиктивных признаков. Однако на будущее отмечу, что в общем случае кодирование правильно настраивать (обучать) на тренировочной выборке (о других предполагаем, что модель ничего не знает), <a href='https://teletype.in/@dt_analytic/yP6vP3B3D6h'> как здесь </a>.

</div>

Разделим датасет на тренировочную и тестовую выборки в соотношении 80/20.

In [10]:
X = df.drop('Price', axis = 1)
y = df['Price']

X_ohe = df_ohe.drop('Price', axis = 1)
y_ohe = df_ohe['Price']

In [11]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 42)

X_train_ohe, X_test_ohe, y_train_ohe, y_test_ohe = train_test_split(X_ohe, y_ohe, test_size = 0.2, random_state = 42)

<b>Дерево принятий решений</b>

Подберем оптимальные гиперпараметры для дерева принятий решений. Для этого будем использовать GridSearchCV

In [12]:
%%time
model_DT = DecisionTreeRegressor(random_state = 42)
params_DT = {
    'max_depth' : list(range(16, 41, 8)),
    'min_samples_leaf' : list(range(3, 9))
}
grid_DT = GridSearchCV(model_DT, params_DT, scoring = 'neg_mean_squared_error', n_jobs = -1, cv = 3)
grid_DT.fit(X_train_ohe, y_train_ohe)

CPU times: user 4min 11s, sys: 16.9 s, total: 4min 28s
Wall time: 4min 29s


GridSearchCV(cv=3, estimator=DecisionTreeRegressor(random_state=42), n_jobs=-1,
             param_grid={'max_depth': [16, 24, 32, 40],
                         'min_samples_leaf': [3, 4, 5, 6, 7, 8]},
             scoring='neg_mean_squared_error')

In [13]:
grid_DT.best_params_

{'max_depth': 32, 'min_samples_leaf': 8}

In [14]:
(grid_DT.best_score_ * (-1)) ** 0.5

1577.900797132528

In [15]:
%%time
grid_DT.best_estimator_.fit(X_train_ohe, y_train_ohe)

CPU times: user 5.88 s, sys: 201 ms, total: 6.08 s
Wall time: 6.08 s


DecisionTreeRegressor(max_depth=32, min_samples_leaf=8, random_state=42)

In [16]:
%%time
grid_DT.predict(X_train_ohe)

CPU times: user 219 ms, sys: 203 ms, total: 422 ms
Wall time: 431 ms


array([ 493.94444444, 1076.03597122, 3443.5       , ...,  795.625     ,
        678.71111111, 3304.09259259])

In [17]:
results_DT = pd.DataFrame(grid_DT.cv_results_).sort_values(by = 'rank_test_score')
results_DT

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
17       3.646739      0.049942         0.138335        0.002967   
11       3.412967      0.075469         0.130021        0.001174   
23       3.749152      0.077899         0.140986        0.005897   
22       3.686941      0.032615         0.141575        0.006638   
16       3.624520      0.034396         0.133003        0.001120   
10       3.417055      0.036595         0.129228        0.001422   
9        3.457271      0.038454         0.132011        0.000532   
15       3.779798      0.109267         0.135492        0.001079   
21       3.459141      0.052057         0.132255        0.004801   
8        3.403358      0.036791         0.130841        0.002034   
14       3.713398      0.050437         0.137486        0.004375   
20       3.605845      0.078810         0.140277        0.004783   
5        3.109231      0.038280         0.122944        0.000681   
4        3.173336      0.080619         0.124951        0.001807   
7        3.492377      0.040753         0.132780        0.000610   
3        3.265902      0.066001         0.130748        0.002419   
13       3.756936      0.093660         0.134717        0.002521   
19       3.737649      0.013472         0.139260        0.005478   
2        3.325054      0.137628         0.131336        0.003920   
1        3.291565      0.099286         0.127882        0.003239   
0        3.156619      0.022905         0.126016        0.001812   
6        3.520189      0.120886         0.134703        0.003023   
12       3.812957      0.093051         0.137762        0.001502   
18       3.893199      0.050455         0.140203        0.000614   

   param_max_depth param_min_samples_leaf  \
17              32                      8   
11              24                      8   
23              40                      8   
22              40                      7   
16              32                      7   
10              24                      7   
9               24                      6   
15              32                      6   
21              40                      6   
8               24                      5   
14              32                      5   
20              40                      5   
5               16                      8   
4               16                      7   
7               24                      4   
3               16                      6   
13              32                      4   
19              40                      4   
2               16                      5   
1               16                      4   
0               16                      3   
6               24                      3   
12              32                      3   
18              40                      3   

                                      params  split0_test_score  \
17  {'max_depth': 32, 'min_samples_leaf': 8}      -2.508785e+06   
11  {'max_depth': 24, 'min_samples_leaf': 8}      -2.510880e+06   
23  {'max_depth': 40, 'min_samples_leaf': 8}      -2.509020e+06   
22  {'max_depth': 40, 'min_samples_leaf': 7}      -2.529275e+06   
16  {'max_depth': 32, 'min_samples_leaf': 7}      -2.530190e+06   
10  {'max_depth': 24, 'min_samples_leaf': 7}      -2.534709e+06   
9   {'max_depth': 24, 'min_samples_leaf': 6}      -2.540611e+06   
15  {'max_depth': 32, 'min_samples_leaf': 6}      -2.539275e+06   
21  {'max_depth': 40, 'min_samples_leaf': 6}      -2.539593e+06   
8   {'max_depth': 24, 'min_samples_leaf': 5}      -2.579103e+06   
14  {'max_depth': 32, 'min_samples_leaf': 5}      -2.579051e+06   
20  {'max_depth': 40, 'min_samples_leaf': 5}      -2.580431e+06   
5   {'max_depth': 16, 'min_samples_leaf': 8}      -2.573485e+06   
4   {'max_depth': 16, 'min_samples_leaf': 7}      -2.593123e+06   
7   {'max_depth': 24, 'min_samples_leaf': 4}      -2.591402e+06   
3   {'max_depth': 16, 'min_samples_leaf': 6}      -2.599277e+06   
13  {'max_depth': 32, 'min_samples_lea

<b>CatBoost</b>

In [18]:
%%time
cat_features = ['VehicleType', 'Gearbox', 'Model', 'FuelType', 'Brand', 'Repaired']
cat = CatBoostRegressor(random_state = 42, cat_features = cat_features, loss_function='RMSE')
params_cat = {
    'depth' : [4, 8],
    'learning_rate': [0.1, 0.2]
}
grid_cat = GridSearchCV(cat, params_cat, cv = 3, n_jobs = -1, scoring = 'neg_mean_squared_error', verbose = 3)
grid_cat.fit(X_train, y_train)

Fitting 3 folds for each of 4 candidates, totalling 12 fits
0:	learn: 3367.2053007	total: 160ms	remaining: 2m 40s
1:	learn: 3196.6245682	total: 255ms	remaining: 2m 7s
2:	learn: 3049.9875103	total: 340ms	remaining: 1m 52s
3:	learn: 2925.9758736	total: 423ms	remaining: 1m 45s
4:	learn: 2818.0723213	total: 516ms	remaining: 1m 42s
5:	learn: 2712.3084418	total: 599ms	remaining: 1m 39s
6:	learn: 2619.8737096	total: 694ms	remaining: 1m 38s
7:	learn: 2540.5407216	total: 780ms	remaining: 1m 36s
8:	learn: 2470.2849233	total: 858ms	remaining: 1m 34s
9:	learn: 2407.6381027	total: 944ms	remaining: 1m 33s
10:	learn: 2353.4082622	total: 1.02s	remaining: 1m 31s
11:	learn: 2297.9016152	total: 1.09s	remaining: 1m 30s
12:	learn: 2251.1452225	total: 1.17s	remaining: 1m 28s
13:	learn: 2202.8413344	total: 1.26s	remaining: 1m 28s
14:	learn: 2166.2742714	total: 1.34s	remaining: 1m 28s
15:	learn: 2130.2165405	total: 1.43s	remaining: 1m 28s
16:	learn: 2098.0156352	total: 1.48s	remaining: 1m 25s
17:	learn: 2064.

GridSearchCV(cv=3,
             estimator=<catboost.core.CatBoostRegressor object at 0x7f6ca57525e0>,
             n_jobs=-1,
             param_grid={'depth': [4, 8], 'learning_rate': [0.1, 0.2]},
             scoring='neg_mean_squared_error', verbose=3)

In [19]:
grid_cat.best_params_

{'depth': 8, 'learning_rate': 0.2}

In [20]:
(grid_cat.best_score_ * (-1)) ** 0.5

1406.9447506807112

In [21]:
%%time
grid_cat.best_estimator_.fit(X_train, y_train)

0:	learn: 3102.6775449	total: 347ms	remaining: 5m 46s
1:	learn: 2761.4186690	total: 667ms	remaining: 5m 32s
2:	learn: 2502.9072185	total: 942ms	remaining: 5m 13s
3:	learn: 2304.3301252	total: 1.2s	remaining: 4m 58s
4:	learn: 2144.4766973	total: 1.54s	remaining: 5m 6s
5:	learn: 2022.3179719	total: 1.83s	remaining: 5m 3s
6:	learn: 1935.3230750	total: 2.17s	remaining: 5m 7s
7:	learn: 1868.6029335	total: 2.45s	remaining: 5m 4s
8:	learn: 1815.7804561	total: 2.65s	remaining: 4m 51s
9:	learn: 1766.4572615	total: 2.9s	remaining: 4m 47s
10:	learn: 1729.2011487	total: 3.16s	remaining: 4m 43s
11:	learn: 1701.6290331	total: 3.41s	remaining: 4m 40s
12:	learn: 1682.0048186	total: 3.61s	remaining: 4m 34s
13:	learn: 1663.0379092	total: 3.85s	remaining: 4m 30s
14:	learn: 1649.8889297	total: 4.02s	remaining: 4m 23s
15:	learn: 1635.7533634	total: 4.21s	remaining: 4m 18s
16:	learn: 1623.8755592	total: 4.38s	remaining: 4m 13s
17:	learn: 1614.9410084	total: 4.56s	remaining: 4m 8s
18:	learn: 1605.9239462	tot

In [22]:
%%time
grid_cat.predict(X_train)

CPU times: user 2.77 s, sys: 12.2 ms, total: 2.78 s
Wall time: 2.79 s


array([ 416.08844713, 1407.2477725 , 3034.78912375, ...,  715.27418444,
        708.79128671, 3272.80951345])

In [23]:
results_cat = pd.DataFrame(grid_cat.cv_results_).sort_values(by = 'rank_test_score')
results_cat

mean_fit_time  std_fit_time  mean_score_time  std_score_time param_depth  \
3     167.618866      6.978941         1.056809        0.095717           8   
2     160.305169      4.533727         0.842400        0.050757           8   
1      74.050733      0.558322         0.437094        0.015321           4   
0      70.637838      0.988398         0.325171        0.014007           4   

  param_learning_rate                              params  split0_test_score  \
3                 0.2  {'depth': 8, 'learning_rate': 0.2}      -1.975851e+06   
2                 0.1  {'depth': 8, 'learning_rate': 0.1}      -1.994250e+06   
1                 0.2  {'depth': 4, 'learning_rate': 0.2}      -2.101191e+06   
0                 0.1  {'depth': 4, 'learning_rate': 0.1}      -2.148784e+06   

   split1_test_score  split2_test_score  mean_test_score  std_test_score  \
3      -1.970697e+06      -1.991933e+06    -1.979494e+06     9043.946702   
2      -1.978752e+06      -2.002010e+06    -1.991671e+06     9668.558735   
1      -2.095354e+06      -2.101406e+06    -2.099317e+06     2803.919371   
0      -2.147935e+06      -2.157405e+06    -2.151374e+06     4278.205276   

   rank_test_score  
3                1  
2                2  
1                3  
0                4

<b>LightGBM</b>

In [24]:
%%time
#чтобы LGBM смог "переварить" категориальные данные, нужно их тип выставить в category: 
categorical = ['VehicleType', 'Gearbox', 'Model', 'FuelType', 'Brand', 'Repaired']
X_train[categorical] = X_train[categorical].astype('category')
X_test[categorical] = X_test[categorical].astype('category')

params_lgbm = {
    'max_depth' : [4, 8], 
    'learning_rate': [0.1, 0.2]
}
lgbm = LGBMRegressor(random_state = 42)
grid_lgbm = GridSearchCV(lgbm, params_lgbm, cv = 3, n_jobs = -1, scoring = 'neg_mean_squared_error', verbose = 3)
grid_lgbm.fit(X_train, y_train)

Fitting 3 folds for each of 4 candidates, totalling 12 fits
[CV 1/3] END .................learning_rate=0.1, max_depth=4; total time= 2.4min
[CV 2/3] END .................learning_rate=0.1, max_depth=4; total time= 2.9min
[CV 3/3] END .................learning_rate=0.1, max_depth=4; total time= 2.6min
[CV 1/3] END .................learning_rate=0.1, max_depth=8; total time= 5.1min
[CV 2/3] END .................learning_rate=0.1, max_depth=8; total time= 6.7min
[CV 3/3] END .................learning_rate=0.1, max_depth=8; total time= 6.8min
[CV 1/3] END .................learning_rate=0.2, max_depth=4; total time= 2.2min
[CV 2/3] END .................learning_rate=0.2, max_depth=4; total time= 2.1min
[CV 3/3] END .................learning_rate=0.2, max_depth=4; total time= 2.5min
[CV 1/3] END .................learning_rate=0.2, max_depth=8; total time= 4.8min
[CV 2/3] END .................learning_rate=0.2, max_depth=8; total time= 5.0min
[CV 3/3] END .................learning_rate=0.2, 

GridSearchCV(cv=3, estimator=LGBMRegressor(random_state=42), n_jobs=-1,
             param_grid={'learning_rate': [0.1, 0.2], 'max_depth': [4, 8]},
             scoring='neg_mean_squared_error', verbose=3)

In [25]:
grid_lgbm.best_params_

{'learning_rate': 0.2, 'max_depth': 8}

In [26]:
(grid_lgbm.best_score_ * (-1)) ** 0.5

1435.3158127011789

In [27]:
%%time
grid_lgbm.best_estimator_.fit(X_train, y_train)

CPU times: user 5min 8s, sys: 2.97 s, total: 5min 11s
Wall time: 5min 14s


LGBMRegressor(learning_rate=0.2, max_depth=8, random_state=42)

In [28]:
%%time
grid_lgbm.predict(X_train)

CPU times: user 1.66 s, sys: 0 ns, total: 1.66 s
Wall time: 1.71 s


array([ 360.60070936, 1066.54728873, 3365.48558586, ...,  660.38076452,
        717.44068554, 3446.38396902])

In [29]:
results_lgbm = pd.DataFrame(grid_lgbm.cv_results_).sort_values(by = 'rank_test_score')
results_lgbm

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
3     333.233455     56.582800         0.675272        0.033715   
1     370.929284     47.131114         0.815674        0.081830   
2     134.812821      9.556263         0.541934        0.034746   
0     157.263139     11.766952         0.548940        0.040780   

  param_learning_rate param_max_depth                                  params  \
3                 0.2               8  {'learning_rate': 0.2, 'max_depth': 8}   
1                 0.1               8  {'learning_rate': 0.1, 'max_depth': 8}   
2                 0.2               4  {'learning_rate': 0.2, 'max_depth': 4}   
0                 0.1               4  {'learning_rate': 0.1, 'max_depth': 4}   

   split0_test_score  split1_test_score  split2_test_score  mean_test_score  \
3      -2.064817e+06      -2.042725e+06      -2.072852e+06    -2.060131e+06   
1      -2.097153e+06      -2.090097e+06      -2.102642e+06    -2.096630e+06   
2      -2.149698e+06      -2.152403e+06      -2.177116e+06    -2.159739e+06   
0      -2.256187e+06      -2.251524e+06      -2.274695e+06    -2.260802e+06   

   std_test_score  rank_test_score  
3    12737.567776                1  
1     5134.742952                2  
2    12336.834953                3  
0    10006.387399                4

## Анализ моделей

<b>Наилучший результат показал CatBoost</b>

In [31]:
%%time
predictions_cat = grid_cat.best_estimator_.predict(X_test)
print('RMSE для CatBoost:', mean_squared_error(y_test, predictions_cat, squared = False))

RMSE для CatBoost: 1394.361995857257
CPU times: user 678 ms, sys: 185 µs, total: 678 ms
Wall time: 678 ms


<b>Вывод:</b>
1. Наилучший результат показал CatBoost, наихудший - дерево принятий решений.
2. Быстрее всех обучается CatBoost, дольше всех - LightGBM.
3. Быстрее всех предсказывает дерево решений, дольше всех - LightGBM
4. Все метрики справились с поставленной задачей и смогли достичь результата RMSE <2500.
5. Так как самыми важными характеристиками является качество и скорость предсказывания, следует обратить внимание на CatBoost и поиграться с его гиперпараметрами для улучшения качества модели. Также стоит сравнивать эти результаты с LightGBM. Дерево принятий решений не рекомендуется использовать для решения данной задачи. Большим минусом является то, что он не умеет работать с категориальными признаками, что повышает время обучения и предсказывания модели.

## Чек-лист проверки

Поставьте 'x' в выполненных пунктах. Далее нажмите Shift+Enter.

- [x]  Jupyter Notebook открыт
- [x]  Весь код выполняется без ошибок
- [x]  Ячейки с кодом расположены в порядке исполнения
- [x]  Выполнена загрузка и подготовка данных
- [x]  Выполнено обучение моделей
- [x]  Есть анализ скорости работы и качества моделей